In [1]:
from crewai import Agent, Task, Crew
from crewai.llm import LLM
import os

# FODS System Description
# ---- SYSTEM DESCRIPTION ----
system_description = """
A food order and delivery system should offer a convenient and efficient way for users to explore, order, and receive meals from a wide range of local and international cuisines. It should provide an accessible and easy-to-navigate interface, available on both web and mobile platforms, where users can browse menus, read reviews, and customize orders to their preferences. The system should feature real-time order tracking, estimated delivery times, and notifications to keep users updated from the moment an order is placed until it is delivered. Integration with various payment gateways should ensure secure and flexible payment options. Additionally, the system should support promotional features, loyalty programs, and personalized recommendations based on user preferences and order history, enhancing the overall user experience and encouraging repeat business.
"""

# Initialize LLM
llm = LLM(
    provider="ollama",
    model="ollama/llama3",  # Corrected model name
    base_url="http://localhost:11434",
    stream=False,
    config={"verbose": True}  # Added verbose logging for debugging
)

# Define Agents
requirements_identifier_agent = Agent(
    name="Requirements Identifier",
    role="Requirements Identification Expert",
    goal="Identify and categorize precise, atomic, and clearly distinguished functional and non-functional system requirements based on provided system descriptions.",
    backstory="A highly analytical requirements specialist, experienced in defining explicit, atomic, and clearly categorized system requirements that accurately address both functional and non-functional system aspects, ensuring consistency and clarity.",
    llm=llm,
    verbose=True
)

use_case_modeler_agent = Agent(
    name="Use Case Modeler",
    role="Use Case Modeling Expert",
    goal="Develop comprehensive and clear use case models, accurately defining system boundaries, actors, use cases, and their logical interactions to ensure all requirements are effectively captured and represented.",
    backstory="An accomplished use case modeling expert known for meticulously creating use case diagrams that clearly illustrate complete system functionalities and actor interactions, accurately aligning them with system requirements.",
    llm=llm,
    verbose=True
)

use_case_specification_agent = Agent(
    name="Use Case Specification Expert",
    role="Use Case Specification Specialist",
    goal="Write detailed, clear, and logically structured use case specifications, accurately describing actor-system interactions, primary and alternative scenarios, and pre/post conditions for each identified use case.",
    backstory="A dedicated expert in use case specification with substantial experience producing systematic, clear, and structured documentation of interactions and scenarios, effectively bridging the gap between analysis and detailed system design.",
    llm=llm,
    verbose=True
)

domain_modeling_agent = Agent(
    name="Domain Modeling Expert",
    role="Domain Model Specialist",
    goal="Create precise and concise domain models clearly representing meaningful domain concepts, relationships, multiplicities, and attributes based on detailed use case specifications, without introducing design-specific decisions.",
    backstory="A proficient domain modeling specialist with deep expertise in translating use case specifications into clear domain representations, accurately modeling real-world concepts and their interrelations while maintaining abstraction suitable for early system modeling phases.",
    llm=llm,
    verbose=True
)

system_operations_agent = Agent(
    name="System Operations Expert",
    role="System Operations Specialist",
    goal="Identify and define clear and accurate system operations, providing correct operation signatures with specified parameters and return types, derived systematically from use case specifications.",
    backstory="A highly skilled system operations analyst, expert at extracting clear operation definitions from use case details, ensuring precision in operation signatures, parameter definitions, and expected outcomes to effectively guide system design and implementation phases.",
    llm=llm,
    verbose=True
)

sequence_diagram_agent = Agent(
    name="Sequence Diagram Expert",
    role="Sequence Diagram Specialist",
    goal="Develop detailed, logical, and accurate design sequence diagrams that precisely depict object interactions, message flows, and collaborations to successfully realize identified system operations.",
    backstory="An expert sequence diagram designer skilled in accurately modeling object lifelines, interactions, and messaging sequences to effectively illustrate logical workflows and operational fulfillment within software systems.",
    llm=llm,
    verbose=True
)

design_class_diagram_agent = Agent(
    name="Design Class Diagram Expert",
    role="Design Class Diagram Specialist",
    goal="Create coherent and comprehensive design class diagrams, clearly defining classes, attributes, operations, relationships, navigabilities, visibilities, data types, and adhering strictly to design principles such as encapsulation and cohesion.",
    backstory="A highly experienced class diagram specialist known for systematically translating domain and sequence diagrams into robust, maintainable class structures, skillfully applying software design best practices and ensuring structural clarity.",
    llm=llm,
    verbose=True
)

implementation_agent = Agent(
    name="Implementation Expert",
    role="Implementation Specialist",
    goal="Develop robust and accurate software implementations strictly aligned with specified design class and sequence diagrams, ensuring adherence to defined method signatures, relationships, object interactions, visibility rules, and logical algorithms.",
    backstory="An accomplished software implementation specialist with extensive experience translating detailed design diagrams into syntactically correct, logically structured, and robust Java code, committed to precise implementation, secure application structures, and adherence to designed specifications.",
    llm=llm,
    verbose=True
)

testing_agent = Agent(
    name="Testing Specialist",
    role="Testing Expert",
    goal="Execute thorough and comprehensive software testing, including unit, integration, and system tests, ensuring full alignment with implementation requirements, accurate object interactions, and system behavior correctness.",
    backstory="A meticulous testing professional with significant expertise in designing, structuring, and executing detailed test scenarios across multiple levels—unit, integration, and system—consistently ensuring system reliability, functionality accuracy, and validation of specified input and output criteria.",
    llm=llm,
    verbose=True
)

# Reviewer Agents
requirements_identifier_reviewer_agent = Agent(
    name="Requirements Reviewer",
    role="Requirements Engineering Reviewer",
    goal="Review identified requirements for clarity, completeness, correct categorization, and traceability to the provided system description. Provide specific, actionable feedback if any improvement is needed.",
    backstory="A meticulous requirements analyst renowned for ensuring that all system requirements are clear, actionable, uniquely identified, and fully cover the described system.",
    llm=llm,
    verbose=True
)

use_case_modeler_reviewer_agent = Agent(
    name="Use Case Model Reviewer",
    role="Use Case Model Reviewer",
    goal="Evaluate the use case model for clarity, completeness, and correct use of UML use case diagram notation. Provide detailed revision feedback if necessary.",
    backstory="A senior UML analyst with deep expertise in structuring use case diagrams for maximum clarity and traceability.",
    llm=llm,
    verbose=True
)

use_case_specification_reviewer_agent = Agent(
    name="Use Case Specification Reviewer",
    role="Use Case Specification Reviewer",
    goal="Evaluate use case specifications for structure, completeness, and clarity. Give feedback for improvement if any aspect is lacking.",
    backstory="A use case documentation specialist with a keen eye for completeness and systematic scenario description.",
    llm=llm,
    verbose=True
)

domain_model_reviewer_agent = Agent(
    name="Domain Model Reviewer",
    role="Domain Modeling Reviewer",
    goal="Review the domain model for correctness, completeness, and clarity. If issues exist, return specific feedback for revision; otherwise, explicitly state approval.",
    backstory="An experienced reviewer specializing in evaluating domain models for accuracy, alignment with requirements, and modeling best practices.",
    llm=llm,
    verbose=True
)

system_operations_reviewer_agent = Agent(
    name="System Operations Reviewer",
    role="System Operations Reviewer",
    goal="Review the system operations list for accuracy, completeness, and consistency with the use case specifications. Provide revision feedback if needed, or approve if correct.",
    backstory="A senior analyst ensuring all system operations accurately reflect user actions and requirements.",
    llm=llm,
    verbose=True
)

sequence_diagram_reviewer_agent = Agent(
    name="Sequence Diagram Reviewer",
    role="Sequence Diagram Reviewer",
    goal="Review the sequence diagrams for correct representation of object interactions and operational logic. Provide revision feedback if needed, or approve if correct.",
    backstory="A methodical diagram reviewer specializing in ensuring the accuracy of object interactions and message flows in sequence diagrams.",
    llm=llm,
    verbose=True
)

design_class_diagram_reviewer_agent = Agent(
    name="Design Class Diagram Reviewer",
    role="Class Diagram Reviewer",
    goal="Review the design class diagram for correct structure, relationships, and adherence to design principles. Provide detailed revision feedback or approve as appropriate.",
    backstory="A class diagram reviewer with deep experience in design principles and structural consistency.",
    llm=llm,
    verbose=True
)

implementation_reviewer_agent = Agent(
    name="Implementation Reviewer",
    role="Implementation Reviewer",
    goal="Assess software implementation for correctness, alignment with design diagrams, and code quality. Give precise, actionable revision feedback as needed.",
    backstory="A seasoned software architect and code reviewer with a reputation for ensuring implementations match design and are robust, maintainable, and error-free.",
    llm=llm,
    verbose=True
)

testing_reviewer_agent = Agent(
    name="Testing Reviewer",
    role="Test Suite Reviewer",
    goal="Check the thoroughness, clarity, and structure of the provided test suite, ensuring full coverage and best practices.",
    backstory="A veteran software tester specializing in test completeness, clarity, and systematic validation.",
    llm=llm,
    verbose=True
)

# Task Definitions with Iterative Review
max_iterations = 5

# ---- 1. REQUIREMENTS IDENTIFICATION ----
feedback = ""
approved = False
final_requirements = None
requirements_output = None
max_retries = 5  # Maximum retries for invalid outputs per iteration

def strip_thought_block(output: str) -> str:
    """Strip trailing 'Thought:' or similar LLM commentary from output, returning only the requirements list."""
    lower = output.lower()
    idx = lower.find("thought:")
    return output[:idx].strip() if idx != -1 else output.strip()

def is_valid_requirements_list(output: str) -> bool:
    """Validate if the output is a valid requirements list, ignoring any trailing 'Thought:'."""
    main = strip_thought_block(output)
    if not main or len(main) < 50:
        return False
    return (
        "FR" in main or "NFR" in main or 
        "Functional Requirements" in main or "Non-Functional Requirements" in main
    )

last_attempted_requirements_output = None  # Store last attempted output
last_nontrivial_requirements_output = None  # Store best non-trivial output
last_nontrivial_length = 0                  # Track length of best nontrivial output

for iteration in range(max_iterations):
    print(f"\n--- Requirements Identification Iteration {iteration+1} ---")
    if not system_description:
        print("Error: No valid system description available. Skipping to next iteration.")
        feedback = "No valid system description provided. Ensure system description is available."
        continue

    requirements_output = None

    # Retry loop for invalid outputs
    for retry in range(max_retries):
        desc = (
            "### System Description\n"
            f"{system_description.strip()}\n\n"
            "### Task\n"
            "Identify and categorize functional and non-functional requirements for the above system. "
            "Produce a structured text list with uniquely identified requirements, categorized as Functional Requirements (FR) and Non-Functional Requirements (NFR). "
            "Each requirement must have a unique ID (e.g., FR1, NFR1) and a clear description.\n"
            "\nGuidelines:\n"
            "- Functional requirements describe specific system actions (e.g., 'User can perform an action').\n"
            "- Non-functional requirements describe system qualities or constraints (e.g., 'System must ensure secure operations').\n"
            "- Use a clear, organized format, e.g.:\n"
            "  Functional Requirements:\n"
            "    FR1: User can perform an action with specified parameters.\n"
            "    FR2: User can view activity history.\n"
            "  Non-Functional Requirements:\n"
            "    NFR1: System must ensure secure operations.\n"
            "    NFR2: System response time must be under 2 seconds.\n"
            "Ensure all requirements are clear, traceable to the system description, and categorized appropriately.\n"
        )
        if feedback:
            desc += f"\n\n### Reviewer Feedback to Address\n{feedback.strip()}\n"

        task1 = Task(
            description=desc,
            agent=requirements_identifier_agent,
            expected_output="A structured text list of uniquely identified functional (FR) and non-functional (NFR) requirements, categorized by features and quality attributes, traceable to the system description.",
        )
        crew = Crew(
            agents=[requirements_identifier_agent],
            tasks=[task1],
            verbose=True
        )
        
        print(f"Attempt {retry+1}/{max_retries} for Requirements Identification")
        try:
            result = crew.kickoff()
            requirements_output = result.tasks_output[0].raw if result.tasks_output else ""
            last_attempted_requirements_output = requirements_output  # Always update this, even if invalid

            # Only update best nontrivial if this is longer and valid after stripping 'Thought:'
            main_content = strip_thought_block(requirements_output)
            if (
                main_content
                and len(main_content) > last_nontrivial_length
                and is_valid_requirements_list(requirements_output)
            ):
                last_nontrivial_requirements_output = requirements_output
                last_nontrivial_length = len(main_content)

            if is_valid_requirements_list(requirements_output):
                print(f"Requirements Agent Output:\n{requirements_output}")
                break  # Valid output, proceed to review
            else:
                print(f"Invalid Requirements Output: {requirements_output}")
                feedback = (
                    "Invalid or empty requirements list. Ensure output is a structured text list with FR and NFR categories, "
                    "unique IDs, and clear descriptions as shown in the example."
                )
        except Exception as e:
            print(f"Error in Requirements Identification Execution: {str(e)}")
            feedback = f"Execution failed: {str(e)}. Ensure output is a structured text list with FR and NFR categories."
            if retry < max_retries - 1:
                print("Retrying...")
                continue
            else:
                print("Max retries reached for this iteration.")
                requirements_output = ""
    
    # Do NOT assign to final_requirements inside the loop; wait until the very end.
    if not is_valid_requirements_list(requirements_output):
        print("Error: No valid requirements list produced after retries. Continuing to next iteration.")
        feedback = (
            "No valid requirements list produced. Ensure output is a structured text list with FR and NFR categories, "
            "unique IDs, and clear descriptions."
        )
        continue

    review_desc = (
        f"Review the following requirements list:\n{requirements_output}\n"
        "Ensure it meets these criteria:\n"
        "- All requirements are uniquely identified with IDs (e.g., FR1, NFR1).\n"
        "- Functional requirements (FR) are grouped by feature and describe specific system actions.\n"
        "- Non-functional requirements (NFR) are grouped by quality attribute and describe system qualities or constraints.\n"
        "- No requirement is ambiguous, overlapping, or missing.\n"
        "- All requirements are traceable to the system description.\n"
        "- The list is well-organized with clear categorization and concise language.\n"
        "Return 'APPROVED' if all criteria are met, or 'REJECTED: [specific feedback]' if revisions are needed. "
        "If the output is empty, lacks a structured list (e.g., contains only thoughts like 'Thought:'), or does not include categorized FR and NFR with unique IDs, return 'REJECTED: No valid requirements list provided. Output must be a structured text list with FR and NFR categories.'"
    )
    review_task = Task(
        description=review_desc,
        agent=requirements_identifier_reviewer_agent,
        expected_output="Either 'APPROVED' or 'REJECTED: [specific feedback]'",
        context=[task1]
    )
    review_crew = Crew(
        agents=[requirements_identifier_reviewer_agent],
        tasks=[review_task],
        verbose=True
    )
    try:
        review_result = review_crew.kickoff()
        review_output = review_result.tasks_output[0].raw if review_result.tasks_output else ""
        if not review_output:
            print("Error: Requirements Review produced no output.")
            feedback = "Reviewer failed to produce an output. Ensure the review task is clear and the LLM is functioning."
            continue
        print(f"Requirements Reviewer Output:\n{review_output}")
    except Exception as e:
        print(f"Error in Requirements Review: {str(e)}")
        feedback = f"Review failed: {str(e)}. Ensure reviewer produces 'APPROVED' or 'REJECTED: [feedback]'."
        continue

    # Only approve if BOTH reviewer and model output are valid
    if "APPROVED" in review_output and is_valid_requirements_list(requirements_output):
        final_requirements = requirements_output
        print("✅ Requirements Approved!")
        approved = True
        break
    else:
        feedback = review_output.replace("REJECTED:", "").strip() if review_output else "No review output provided."
        print("🔄 Reviewer requested revisions.")

# --- Robust Fallback assignment after all iterations ---
if not final_requirements or not strip_thought_block(final_requirements):
    if last_nontrivial_requirements_output and strip_thought_block(last_nontrivial_requirements_output):
        final_requirements = last_nontrivial_requirements_output
        print("⚠️ Using best nontrivial rejected output as fallback!")
    elif last_attempted_requirements_output and strip_thought_block(last_attempted_requirements_output):
        final_requirements = last_attempted_requirements_output
        print("⚠️ Using last attempted output as fallback!")
    else:
        final_requirements = ""
        print("❌ No requirements list could be generated.")

print("\n====== FINAL REQUIREMENTS LIST OUTPUT ======")
main_content = strip_thought_block(final_requirements) if final_requirements else ""
if main_content:
    print(main_content)
else:
    print("(No valid requirements list generated. See above logs.)")

# ---- 2. USE CASE MODELING ----
feedback = ""
approved = False
final_use_case_model = None
use_case_model_output = None
max_retries = 5  # Maximum retries for invalid outputs per iteration

def strip_thought_block(output: str) -> str:
    """Strip trailing 'Thought:' or similar commentary, returning only the diagram/code block."""
    if not output:
        return ""
    lower = output.lower()
    idx = lower.find("thought:")
    return output[:idx].strip() if idx != -1 else output.strip()

def is_valid_use_case_model(output: str) -> bool:
    """Validate if the output is a valid use case model with a diagram code block (ignoring trailing Thought:)."""
    main = strip_thought_block(output)
    if not main or len(main) < 50:
        return False
    diagram_starts = [
        "@startuml",               # PlantUML
        "```plantuml",             # Markdown PlantUML block
        "```uml",                  # Markdown UML block
        "```mermaid",              # Mermaid diagram
        "+------",                 # ASCII-art diagram start (rough heuristic)
        "|",                       # More ASCII-art (use with caution)
        "usecase",                 # PlantUML
        "actor ",                  # PlantUML/Mermaid
        "<</",                     # PlantUML stereotypes like <<include>>, <<extend>>
    ]
    return any(start in main for start in diagram_starts)

last_attempted_use_case_model_output = None  # Stores the most recent output each retry
last_nontrivial_use_case_model_output = None  # Stores the last plausible diagram
last_nontrivial_length = 0  # Track length of best nontrivial output

for iteration in range(max_iterations):
    print(f"\n--- Use Case Modeling Iteration {iteration+1} ---")
    if not final_requirements and not requirements_output:
        print("Error: No valid requirements available. Skipping to next iteration.")
        feedback = "No valid requirements provided. Ensure requirements are available."
        continue

    use_case_model_output = None

    for retry in range(max_retries):
        desc = (
            f"Using the list of functional and non-functional requirements from the previous task, create a **UML use case diagram** for the system. "
            "Follow standard UML graphical notation:\n"
            "- Draw the system boundary as a rectangle with the system name at the top.\n"
            "- Place actors outside the system boundary as stick figures, labeled with their role names.\n"
            "- Use cases are shown as ovals inside the system boundary, each with a unique ID and descriptive name.\n"
            "- Draw solid lines (associations) between actors and the use cases they interact with.\n"
            "- Depict <<include>> and <<extend>> relationships using dashed arrows labeled with the respective stereotype.\n"
            "- Ensure each use case is traceable to the requirements and all necessary actors, use cases, and relationships are included.\n"
            "Any text-based notation—output should be in clear, standard UML diagram format.\n"
            "The diagram should clearly depict:\n"
            "  * System boundary (rectangle)\n"
            "  * Stick figure actors (outside)\n"
            "  * Ovals for use cases (inside)\n"
            "  * Association lines between actors and use cases\n"
            "  * <<include>> or <<extend>> with correct stereotypes if used\n"
            "  * Unique identifiers for each use case (e.g., UC1, UC2)\n"
        )
        if feedback:
            desc += f"\nReviewer feedback to address: {feedback}\n"

        # Summarize inputs to avoid context overflow
        if final_requirements:
            desc += f"Requirements (summary): {str(final_requirements)[:500]}...\n"
        else:
            desc += f"Latest Requirements (summary): {str(requirements_output)[:500]}...\n" if requirements_output else "No requirements available.\n"

        task2 = Task(
            description=desc,
            agent=use_case_modeler_agent,
            expected_output="A UML use case model diagram in standard UML graphical notation, depicting system boundaries, actor interactions, relationships, and uniquely identified use cases, consistent with the requirements.",
            context=[task1]
        )
        crew = Crew(
            agents=[use_case_modeler_agent],
            tasks=[task2],
            verbose=True
        )

        print(f"Attempt {retry+1}/{max_retries} for Use Case Model Generation")
        try:
            result = crew.kickoff()
            use_case_model_output = result.tasks_output[0].raw if result.tasks_output else ""
            last_attempted_use_case_model_output = use_case_model_output  # Always update with each retry

            main_content = strip_thought_block(use_case_model_output)
            if (
                main_content
                and len(main_content) > last_nontrivial_length
                and is_valid_use_case_model(use_case_model_output)
            ):
                last_nontrivial_use_case_model_output = use_case_model_output
                last_nontrivial_length = len(main_content)

            if is_valid_use_case_model(use_case_model_output):
                print(f"Use Case Model Agent Output:\n{use_case_model_output}")
                break  # Valid output, proceed to review
            else:
                print(f"Invalid Use Case Model Output: {use_case_model_output}")
                feedback = "Invalid or empty use case model. Ensure output is in standard UML diagrammatic form, with actors, use cases, and associations, as described."
                if retry < max_retries - 1:
                    print("Retrying with feedback...")
                else:
                    print("Max retries reached for this iteration.")
        except Exception as e:
            print(f"Error in Use Case Model Execution: {str(e)}")
            feedback = f"Execution failed: {str(e)}. Ensure output is in standard UML use case diagram notation."
            if retry < max_retries - 1:
                print("Retrying...")
                continue
            else:
                print("Max retries reached for this iteration.")
                use_case_model_output = ""

    # If no valid output, do not immediately overwrite final_use_case_model
    if not is_valid_use_case_model(use_case_model_output):
        print("Error: No valid use case model produced after retries. Continuing to next iteration.")
        feedback = "No valid use case model produced. Ensure output follows standard UML notation with actors, use cases, and associations."
        continue

    # Review step
    review_desc = (
        f"Review the following use case model diagram:\n{use_case_model_output}\n"
        "Ensure it meets these criteria:\n"
        "- System boundary is clearly shown and labeled.\n"
        "- All actors (primary and secondary) are identified as stick figures outside the system boundary and connected to relevant use cases with lines.\n"
        "- All system functionalities from requirements are captured as use cases with unique IDs/names, drawn as ovals inside the system boundary.\n"
        "- Association lines connect actors to use cases; <<include>> and <<extend>> relationships are used correctly and labeled appropriately if applicable.\n"
        "- Diagram is clear, uncluttered, and legible.\n"
        "- Use cases and actors are traceable to requirements.\n"
        "- Follows UML notation: actors as stick figures outside the system boundary (rectangle), use cases as ovals inside, associations as lines.\n"
        "Return 'APPROVED' if all criteria are met, or 'REJECTED: [specific feedback]' if revisions are needed. "
        "If the output is empty, lacks diagram content, or does not follow UML notation, return 'REJECTED: No valid use case model provided. Output must include a standard UML use case diagram with actors, use cases, and associations.'"
    )
    review_task = Task(
        description=review_desc,
        agent=use_case_modeler_reviewer_agent,
        expected_output="Either 'APPROVED' or 'REJECTED: [specific feedback]'",
        context=[task2]
    )
    review_crew = Crew(
        agents=[use_case_modeler_reviewer_agent],
        tasks=[review_task],
        verbose=True
    )
    try:
        review_result = review_crew.kickoff()
        review_output = review_result.tasks_output[0].raw if review_result.tasks_output else ""
        if not review_output:
            print("Error: Use Case Model Review produced no output.")
            feedback = "Reviewer failed to produce an output. Ensure the review task is clear and the LLM is functioning."
            continue
        print(f"Use Case Model Reviewer Output:\n{review_output}")
    except Exception as e:
        print(f"Error in Use Case Model Review: {str(e)}")
        feedback = f"Review failed: {str(e)}. Ensure reviewer produces 'APPROVED' or 'REJECTED: [feedback]'."
        continue

    if "APPROVED" in review_output and is_valid_use_case_model(use_case_model_output):
        final_use_case_model = use_case_model_output
        print("✅ Use Case Model Approved!")
        approved = True
        break
    else:
        feedback = review_output.replace("REJECTED:", "").strip() if review_output else "No review output provided."
        print("🔄 Reviewer requested revisions.")

# --- Robust fallback assignment after all iterations ---
if not final_use_case_model or not strip_thought_block(final_use_case_model):
    if last_nontrivial_use_case_model_output and strip_thought_block(last_nontrivial_use_case_model_output):
        final_use_case_model = last_nontrivial_use_case_model_output
        print("⚠️ Using best nontrivial rejected output as fallback!")
    elif last_attempted_use_case_model_output and strip_thought_block(last_attempted_use_case_model_output):
        final_use_case_model = last_attempted_use_case_model_output
        print("⚠️ Using last attempted output as fallback!")
    else:
        final_use_case_model = ""
        print("❌ No use case model could be generated.")

print("\n====== FINAL USE CASE MODEL OUTPUT ======")
main_content = strip_thought_block(final_use_case_model) if final_use_case_model else ""
if main_content:
    print(main_content)
else:
    print("(No valid use case model output generated. See above logs.)")




# ---- 3. USE CASE SPECIFICATION ----
feedback = ""
approved = False
final_use_case_spec = None
use_case_spec_output = None
max_retries = 5  # Maximum retries for invalid outputs per iteration

def strip_thought_block(output: str) -> str:
    """Strip trailing 'Thought:' or similar commentary, returning only the actual specification."""
    if not output:
        return ""
    lower = output.lower()
    idx = lower.find("thought:")
    return output[:idx].strip() if idx != -1 else output.strip()

def is_valid_use_case_spec(output: str) -> bool:
    """Validate if the output is a valid use case specification (ignoring trailing Thought:)."""
    main = strip_thought_block(output)
    if not main or len(main) < 50:
        return False
    required_sections = ["Use Case ID", "Use Case Name", "Primary Actor", "Preconditions", "Postconditions", "Main Flow", "Alternative Flows"]
    return any(section in main for section in required_sections)

last_attempted_use_case_spec_output = None  # Store last attempted output
last_nontrivial_use_case_spec_output = None  # Store best nontrivial output
last_nontrivial_length = 0                  # Track length of best nontrivial output

for iteration in range(max_iterations):
    print(f"\n--- Use Case Specification Iteration {iteration+1} ---")
    # Validate prerequisite inputs
    if not final_use_case_model and not use_case_model_output:
        print("Error: No valid use case model available. Skipping to next iteration.")
        feedback = "No valid use case model provided. Ensure use case model is available."
        continue

    use_case_spec_output = None

    for retry in range(max_retries):
        desc = (
            f"Using the use case model from the previous task, develop detailed use case specifications for each identified use case in the system. "
            "Each specification must include Use Case ID, Use Case Name, Primary Actor, Preconditions, Postconditions, Main Flow, and Alternative Flows, clearly illustrating actor-system interactions in a structured text format.\n"
            "Guidelines:\n"
            "- Each use case specification must have a unique ID (e.g., UC1) and a descriptive name.\n"
            "- Primary Actor identifies the main user or system interacting with the use case.\n"
            "- Preconditions and Postconditions describe the system state before and after the use case.\n"
            "- Main Flow outlines the primary scenario of actor-system interactions in numbered steps.\n"
            "- Alternative Flows describe deviations or error cases in numbered steps.\n"
            "- Use a clear, structured format, e.g.:\n"
            "  Use Case ID: UC1\n"
            "  Use Case Name: Perform Action\n"
            "  Primary Actor: User\n"
            "  Preconditions: User is authenticated, system is in a valid state.\n"
            "  Postconditions: Action is completed, system state is updated.\n"
            "  Main Flow:\n"
            "    1. User initiates an action with specified parameters.\n"
            "    2. System validates the action.\n"
            "    3. System updates the relevant data.\n"
            "    4. System records the action.\n"
            "  Alternative Flows:\n"
            "    A1: Invalid parameters\n"
            "      1. System displays error message.\n"
            "      2. Use case ends.\n"
            "Ensure specifications are clear, traceable to the use case model, and cover all required sections.\n"
        )
        if feedback:
            desc += f"\nReviewer feedback to address: {feedback}\n"

        # Summarize inputs to avoid context overflow
        if final_use_case_model:
            desc += f"Use Case Model (summary): {str(final_use_case_model)[:500]}...\n"
        else:
            desc += f"Latest Use Case Model (summary): {str(use_case_model_output)[:500]}...\n" if use_case_model_output else "No use case model available.\n"

        task3 = Task(
            description=desc,
            agent=use_case_specification_agent,
            expected_output="A structured text document of detailed use case specifications, including Use Case ID, Name, Primary Actor, Preconditions, Postconditions, Main Flow, and Alternative Flows for each use case, consistent with the use case model.",
            context=[task2]
        )
        crew = Crew(
            agents=[use_case_specification_agent],
            tasks=[task3],
            verbose=True
        )

        print(f"Attempt {retry+1}/{max_retries} for Use Case Specification Generation")
        try:
            result = crew.kickoff()
            use_case_spec_output = result.tasks_output[0].raw if result.tasks_output else ""
            last_attempted_use_case_spec_output = use_case_spec_output  # Always store the latest output

            main_content = strip_thought_block(use_case_spec_output)
            if (
                main_content
                and len(main_content) > last_nontrivial_length
                and is_valid_use_case_spec(use_case_spec_output)
            ):
                last_nontrivial_use_case_spec_output = use_case_spec_output
                last_nontrivial_length = len(main_content)

            if is_valid_use_case_spec(use_case_spec_output):
                print(f"Use Case Specification Agent Output:\n{use_case_spec_output}")
                break
            else:
                print(f"Invalid Use Case Specification Output: {use_case_spec_output}")
                feedback = "Invalid or empty use case specification. Ensure output is a structured text document with Use Case ID, Name, Primary Actor, Preconditions, Postconditions, Main Flow, and Alternative Flows as shown in the example."
                if retry < max_retries - 1:
                    print("Retrying with feedback...")
                else:
                    print("Max retries reached for this iteration.")
        except Exception as e:
            print(f"Error in Use Case Specification Execution: {str(e)}")
            feedback = f"Execution failed: {str(e)}. Ensure output is a structured text document with required sections."
            if retry < max_retries - 1:
                print("Retrying...")
                continue
            else:
                print("Max retries reached for this iteration.")
                use_case_spec_output = ""

    if not is_valid_use_case_spec(use_case_spec_output):
        print("Error: No valid use case specification produced after retries. Continuing to next iteration.")
        feedback = "No valid use case specification produced. Ensure output is a structured text document with Use Case ID, Name, Primary Actor, Preconditions, Postconditions, Main Flow, and Alternative Flows."
        continue

    review_desc = (
        f"Review the following use case specifications:\n{use_case_spec_output}\n"
        "Ensure they meet these criteria:\n"
        "- Each use case has a unique ID (e.g., UC1) and descriptive name.\n"
        "- Each specification includes Primary Actor, Preconditions, Postconditions, Main Flow, and Alternative Flows.\n"
        "- Main Flow and Alternative Flows are detailed with step-by-step actor-system interactions.\n"
        "- Preconditions and Postconditions are clear, realistic, and reflect system state changes.\n"
        "- Specifications are consistent with the use case model and traceable to its use cases.\n"
        "- The document is well-organized, unambiguous, and complete.\n"
        "Return 'APPROVED' if all criteria are met, or 'REJECTED: [specific feedback]' if revisions are needed. "
        "If the output is empty, lacks structured specification content (e.g., contains only thoughts like 'Thought:'), or does not include required sections, return 'REJECTED: No valid use case specification provided. Output must be a structured text document with required sections.'"
    )
    review_task = Task(
        description=review_desc,
        agent=use_case_specification_reviewer_agent,
        expected_output="Either 'APPROVED' or 'REJECTED: [specific feedback]'",
        context=[task3]
    )
    review_crew = Crew(
        agents=[use_case_specification_reviewer_agent],
        tasks=[review_task],
        verbose=True
    )
    try:
        review_result = review_crew.kickoff()
        review_output = review_result.tasks_output[0].raw if review_result.tasks_output else ""
        if not review_output:
            print("Error: Use Case Specification Review produced no output.")
            feedback = "Reviewer failed to produce an output. Ensure the review task is clear and the LLM is functioning."
            continue
        print(f"Use Case Specification Reviewer Output:\n{review_output}")
    except Exception as e:
        print(f"Error in Use Case Specification Review: {str(e)}")
        feedback = f"Review failed: {str(e)}. Ensure reviewer produces 'APPROVED' or 'REJECTED: [feedback]'."
        continue

    if "APPROVED" in review_output and is_valid_use_case_spec(use_case_spec_output):
        final_use_case_spec = use_case_spec_output
        print("✅ Use Case Specification Approved!")
        approved = True
        break
    else:
        feedback = review_output.replace("REJECTED:", "").strip() if review_output else "No review output provided."
        print("🔄 Reviewer requested revisions.")

# --- Robust fallback assignment after all iterations ---
if not final_use_case_spec or not strip_thought_block(final_use_case_spec):
    if last_nontrivial_use_case_spec_output and strip_thought_block(last_nontrivial_use_case_spec_output):
        final_use_case_spec = last_nontrivial_use_case_spec_output
        print("⚠️ Using best nontrivial rejected output as fallback!")
    elif last_attempted_use_case_spec_output and strip_thought_block(last_attempted_use_case_spec_output):
        final_use_case_spec = last_attempted_use_case_spec_output
        print("⚠️ Using last attempted output as fallback!")
    else:
        final_use_case_spec = ""
        print("❌ No use case specification could be generated.")

print("\n====== FINAL USE CASE SPECIFICATION OUTPUT ======")
main_content = strip_thought_block(final_use_case_spec) if final_use_case_spec else ""
if main_content:
    print(main_content)
else:
    print("(No valid use case specification output generated. See above logs.)")





# ---- 4. DOMAIN MODEL LOOP ----
feedback = ""
approved = False
final_domain_model = None
domain_model_output = None
max_retries = 5  # Maximum retries for invalid outputs per iteration

def strip_thought_block(output: str) -> str:
    """Strip trailing 'Thought:' or similar LLM commentary from output, returning only the diagram."""
    if not output:
        return ""
    lower = output.lower()
    idx = lower.find("thought:")
    return output[:idx].strip() if idx != -1 else output.strip()

def is_valid_domain_model(output: str) -> bool:
    """Strictly validate if the output is a domain model with a real UML diagram or code block (ignoring trailing Thought:)."""
    main = strip_thought_block(output)
    if not main or len(main) < 50:
        return False
    diagram_starts = [
        "@startuml",        # PlantUML start
        "```plantuml",      # Markdown PlantUML code block
        "```uml",           # Markdown UML code block
        "```mermaid",       # Mermaid diagram block
        "classDiagram",     # Mermaid class diagram start
        "+------",          # ASCII-art UML class diagram heuristic
        "|",                # ASCII-art line
        "class ",           # PlantUML/Mermaid class block
        "association",      # PlantUML/Mermaid/other
    ]
    return any(start in main for start in diagram_starts)

last_attempted_domain_model_output = None    # Store last attempted output
last_nontrivial_domain_model_output = None   # Store best non-trivial output
last_nontrivial_length = 0                  # Track length of best nontrivial output

for iteration in range(max_iterations):
    print(f"\n--- Domain Model Iteration {iteration+1} ---")
    if not final_use_case_spec and not use_case_spec_output:
        print("Error: No valid use case specifications available. Skipping to next iteration.")
        feedback = "No valid use case specifications provided. Ensure use case specifications are available."
        continue

    domain_model_output = None

    for retry in range(max_retries):
        desc = (
            f"Based on the detailed use case specifications from the previous task, create a clear and concise **domain model** for the system. "
            "Represent domain concepts as classes, list relevant attributes (without data types or visibility), and show associations and multiplicities using **standard UML class diagram notation** ONLY.\n"
            "Guidelines:\n"
            "- Identify classes from nouns in the use case specifications representing core entities.\n"
            "- List attributes inside each class (rectangle), as simple nouns with no types, visibility, or operations.\n"
            "- Show relationships (associations) between classes as lines, with multiplicity labels (e.g., '1', '0..*') as needed.\n"
            "- Markup—output must be a graphical UML class diagram.\n"
            "- No design-level details (no methods, visibility, data types, navigability, or annotations).\n"
            "Your output must clearly show:\n"
            "  * Each class as a labeled rectangle, with attributes listed inside\n"
            "  * Association lines connecting classes, labeled with multiplicities\n"
            "  * Only domain concepts and associations, no technical or implementation details\n"
        )
        if feedback:
            desc += f"\nReviewer feedback to address: {feedback}\n"

        if final_use_case_spec:
            desc += f"Use Case Specifications (summary): {str(final_use_case_spec)[:500]}...\n"
        else:
            desc += f"Latest Use Case Specifications (summary): {str(use_case_spec_output)[:500]}...\n" if use_case_spec_output else "No use case specifications available.\n"

        task4 = Task(
            description=desc,
            agent=domain_modeling_agent,
            expected_output=(
                "A UML domain model diagram in standard UML class diagram notation, accurately showing classes (as rectangles), their attributes, associations (as lines), and multiplicities, with no design-level details and consistent with the use case specifications. If graphical drawing is not possible, provide a clear, labeled ASCII-art UML class diagram."
            ),
            context=[task3]
        )
        crew = Crew(
            agents=[domain_modeling_agent],
            tasks=[task4],
            verbose=True
        )

        print(f"Attempt {retry+1}/{max_retries} for Domain Model Generation")
        try:
            result = crew.kickoff()
            domain_model_output = result.tasks_output[0].raw if result.tasks_output else ""
            last_attempted_domain_model_output = domain_model_output  # Always update this (may be empty)

            main_content = strip_thought_block(domain_model_output)
            if (
                main_content
                and len(main_content) > last_nontrivial_length
                and is_valid_domain_model(domain_model_output)
            ):
                last_nontrivial_domain_model_output = domain_model_output
                last_nontrivial_length = len(main_content)

            if is_valid_domain_model(domain_model_output):
                print(f"Domain Model Agent Output:\n{domain_model_output}")
                break  # Valid output, proceed to review
            else:
                print(f"Invalid Domain Model Output: {domain_model_output}")
                feedback = (
                    "Invalid or empty domain model. Output must use standard UML class diagram notation (graphical or ASCII), "
                    "with rectangles for classes, attributes listed inside, and labeled associations."
                )
                if retry < max_retries - 1:
                    print("Retrying with feedback...")
                else:
                    print("Max retries reached for this iteration.")
        except Exception as e:
            print(f"Error in Domain Model Execution: {str(e)}")
            feedback = (
                f"Execution failed: {str(e)}. Ensure output is in standard UML class diagram notation, not code."
            )
            if retry < max_retries - 1:
                print("Retrying...")
                continue
            else:
                print("Max retries reached for this iteration.")
                domain_model_output = ""

    # Do NOT assign to final_domain_model inside the loop; assign at the end.
    if not is_valid_domain_model(domain_model_output):
        print("Error: No valid domain model produced after retries. Continuing to next iteration.")
        feedback = (
            "No valid domain model produced. Ensure output follows standard UML graphical or ASCII notation "
            "with rectangles for classes, listed attributes, and association lines labeled with multiplicities."
        )
        continue

    review_desc = (
        f"Review the following domain model:\n{domain_model_output}\n"
        "Ensure it meets these criteria:\n"
        "- All core domain concepts (classes) from the use case specifications are shown as labeled rectangles (e.g., Wallet, Transaction).\n"
        "- Each class lists relevant attributes as simple nouns, with no data types, visibility, or operations.\n"
        "- Relationships are clearly depicted as association lines, with correct multiplicities (e.g., '1', '0..*'), and no navigability or design specifics.\n"
        "- The model avoids design-level elements (no methods, no data types, no annotations).\n"
        "- The model is clear, concise, and traceable to the use case specifications.\n"
        "- Follows standard UML: rectangles for classes/attributes, association lines, multiplicity labels.\n"
        "Return 'APPROVED' if all criteria are met, or 'REJECTED: [specific feedback]' if revisions are needed. "
        "If the output is empty, lacks diagram content, or does not follow UML diagram conventions, return 'REJECTED: No valid domain model provided. Output must be a UML class diagram with classes, attributes, and associations.'"
    )
    review_task = Task(
        description=review_desc,
        agent=domain_model_reviewer_agent,
        expected_output="Either 'APPROVED' or 'REJECTED: [specific feedback]'",
        context=[task4]
    )
    review_crew = Crew(
        agents=[domain_model_reviewer_agent],
        tasks=[review_task],
        verbose=True
    )
    try:
        review_result = review_crew.kickoff()
        review_output = review_result.tasks_output[0].raw if review_result.tasks_output else ""
        if not review_output:
            print("Error: Domain Model Review produced no output.")
            feedback = "Reviewer failed to produce an output. Ensure the review task is clear and the LLM is functioning."
            continue
        print(f"Domain Model Reviewer Output:\n{review_output}")
    except Exception as e:
        print(f"Error in Domain Model Review: {str(e)}")
        feedback = f"Review failed: {str(e)}. Ensure reviewer produces 'APPROVED' or 'REJECTED: [feedback]'."
        continue

    # Only approve if BOTH reviewer and model output are valid
    if "APPROVED" in review_output and is_valid_domain_model(domain_model_output):
        final_domain_model = domain_model_output
        print("✅ Domain Model Approved!")
        approved = True
        break
    else:
        feedback = review_output.replace("REJECTED:", "").strip() if review_output else "No review output provided."
        print("🔄 Reviewer requested revisions.")

# --- Robust Fallback assignment after all iterations ---
if not final_domain_model or not strip_thought_block(final_domain_model):
    if last_nontrivial_domain_model_output and strip_thought_block(last_nontrivial_domain_model_output):
        final_domain_model = last_nontrivial_domain_model_output
        print("⚠️ Using best nontrivial rejected output as fallback!")
    elif last_attempted_domain_model_output and strip_thought_block(last_attempted_domain_model_output):
        final_domain_model = last_attempted_domain_model_output
        print("⚠️ Using last attempted output as fallback!")
    else:
        final_domain_model = ""
        print("❌ No domain model could be generated.")

print("\n====== FINAL DOMAIN MODEL OUTPUT ======")
main_content = strip_thought_block(final_domain_model) if final_domain_model else ""
if main_content:
    print(main_content)
else:
    print("(No valid domain model output generated. See above logs.)")


# ---- 5. SYSTEM OPERATIONS LOOP ----
feedback = ""
approved = False
final_system_operations = None
system_operations_output = None
max_retries = 5  # Maximum retries for invalid outputs per iteration

def strip_thought_block(output: str) -> str:
    """Strip trailing 'Thought:' or similar LLM commentary, returning only the system operations list."""
    if not output:
        return ""
    lower = output.lower()
    idx = lower.find("thought:")
    return output[:idx].strip() if idx != -1 else output.strip()

def is_valid_system_operations_list(output: str) -> bool:
    """Validate if the output is a valid system operations list (ignoring trailing Thought:)."""
    main = strip_thought_block(output)
    if not main or len(main) < 50:
        return False
    return ":" in main and ")" in main and ("system operations" in main or "operation" in main.lower())

last_attempted_system_operations_output = None  # Store last attempted output
last_nontrivial_system_operations_output = None # Store best nontrivial output
last_nontrivial_length = 0                     # Track length of best nontrivial output

for iteration in range(max_iterations):
    print(f"\n--- System Operations Iteration {iteration+1} ---")
    # Validate prerequisite inputs
    if not final_use_case_spec and not use_case_spec_output:
        print("Error: No valid use case specifications available. Skipping to next iteration.")
        feedback = "No valid use case specifications provided. Ensure use case specifications are available."
        continue

    system_operations_output = None

    for retry in range(max_retries):
        desc = (
            f"Using the detailed use case specifications from the previous task, identify system operations for the system. "
            "Provide each operation with a correct signature format (operationName(parameter1: parameterType, ...): returnType), clearly specifying parameter types and return types in a structured text list.\n"
            "Guidelines:\n"
            "- Derive operations from user-initiated actions in the main and alternative flows of the use case specifications.\n"
            "- Each operation must have a clear name, parameters with types, and a return type (e.g., performAction(value: double): boolean).\n"
            "- Exclude system responses; focus only on user-initiated actions.\n"
            "- Use a clear, structured format, e.g.:\n"
            "  System Operations:\n"
            "    - performAction(value: double): boolean\n"
            "    - viewHistory(): List<Record>\n"
            "    - addResource(amount: double): boolean\n"
            "Ensure operations are clear, traceable to the use case specifications, and include proper signatures.\n"
        )
        if feedback:
            desc += f"\nReviewer feedback to address: {feedback}\n"
        
        # Summarize inputs to avoid context overflow
        if final_use_case_spec:
            desc += f"Use Case Specifications (summary): {str(final_use_case_spec)[:500]}...\n"  # Limit to 500 chars
        else:
            desc += f"Latest Use Case Specifications (summary): {str(use_case_spec_output)[:500]}...\n" if use_case_spec_output else "No use case specifications available.\n"
        
        task5 = Task(
            description=desc,
            agent=system_operations_agent,
            expected_output="A structured text list of system operations with accurate signatures (operationName(parameter1: type, ...): returnType), derived from user actions in the use case specifications.",
            context=[task3]
        )
        crew = Crew(
            agents=[system_operations_agent],
            tasks=[task5],
            verbose=True
        )
        
        print(f"Attempt {retry+1}/{max_retries} for System Operations Generation")
        try:
            result = crew.kickoff()
            system_operations_output = result.tasks_output[0].raw if result.tasks_output else ""
            last_attempted_system_operations_output = system_operations_output  # Always update this

            main_content = strip_thought_block(system_operations_output)
            if (
                main_content
                and len(main_content) > last_nontrivial_length
                and is_valid_system_operations_list(system_operations_output)
            ):
                last_nontrivial_system_operations_output = system_operations_output
                last_nontrivial_length = len(main_content)

            if is_valid_system_operations_list(system_operations_output):
                print(f"System Operations Agent Output:\n{system_operations_output}")
                break  # Valid output, proceed to review
            else:
                print(f"Invalid System Operations Output: {system_operations_output}")
                feedback = "Invalid or empty system operations list. Ensure output is a structured text list with operation signatures including parameters and return types as shown in the example."
                if retry < max_retries - 1:
                    print("Retrying with feedback...")
                else:
                    print("Max retries reached for this iteration.")
        except Exception as e:
            print(f"Error in System Operations Execution: {str(e)}")
            feedback = f"Execution failed: {str(e)}. Ensure output is a structured text list with operation signatures."
            if retry < max_retries - 1:
                print("Retrying...")
                continue
            else:
                print("Max retries reached for this iteration.")
                system_operations_output = ""
    
    # Do NOT assign to final_system_operations inside the loop; assign at the end.
    if not is_valid_system_operations_list(system_operations_output):
        print("Error: No valid system operations list produced after retries. Continuing to next iteration.")
        feedback = "No valid system operations list produced. Ensure output is a structured text list with operation signatures including parameters and return types."
        continue

    review_desc = (
        f"Review the following system operations list:\n{system_operations_output}\n"
        "Ensure it meets these criteria:\n"
        "- All operations are derived from user-initiated actions in the use case specifications' main and alternative flows.\n"
        "- Each operation has a correct signature (operationName(parameter1: type, ...): returnType) with clear parameter and return types.\n"
        "- All user-initiated actions are covered; no system responses are included as operations.\n"
        "- The list is free of ambiguity, design-specific elements, and consistent with the use case specifications.\n"
        "- The list is well-organized and traceable to the use case specifications.\n"
        "Return 'APPROVED' if all criteria are met, or 'REJECTED: [specific feedback]' if revisions are needed. "
        "If the output is empty, lacks a structured list (e.g., contains only thoughts like 'Thought:'), or does not include operation signatures, return 'REJECTED: No valid system operations list provided. Output must be a structured text list with operation signatures.'"
    )
    review_task = Task(
        description=review_desc,
        agent=system_operations_reviewer_agent,
        expected_output="Either 'APPROVED' or 'REJECTED: [specific feedback]'",
        context=[task5]
    )
    review_crew = Crew(
        agents=[system_operations_reviewer_agent],
        tasks=[review_task],
        verbose=True
    )
    try:
        review_result = review_crew.kickoff()
        review_output = review_result.tasks_output[0].raw if review_result.tasks_output else ""
        if not review_output:
            print("Error: System Operations Review produced no output.")
            feedback = "Reviewer failed to produce an output. Ensure the review task is clear and the LLM is functioning."
            continue
        print(f"System Operations Reviewer Output:\n{review_output}")
    except Exception as e:
        print(f"Error in System Operations Review: {str(e)}")
        feedback = f"Review failed: {str(e)}. Ensure reviewer produces 'APPROVED' or 'REJECTED: [feedback]'."
        continue

    if "APPROVED" in review_output and is_valid_system_operations_list(system_operations_output):
        final_system_operations = system_operations_output
        print("✅ System Operations Approved!")
        approved = True
        break
    else:
        feedback = review_output.replace("REJECTED:", "").strip() if review_output else "No review output provided."
        print("🔄 Reviewer requested revisions.")

# --- Robust Fallback assignment after all iterations ---
if not final_system_operations or not strip_thought_block(final_system_operations):
    if last_nontrivial_system_operations_output and strip_thought_block(last_nontrivial_system_operations_output):
        final_system_operations = last_nontrivial_system_operations_output
        print("⚠️ Using best nontrivial rejected output as fallback!")
    elif last_attempted_system_operations_output and strip_thought_block(last_attempted_system_operations_output):
        final_system_operations = last_attempted_system_operations_output
        print("⚠️ Using last attempted output as fallback!")
    else:
        final_system_operations = ""
        print("❌ No system operations list could be generated.")

print("\n====== FINAL SYSTEM OPERATIONS OUTPUT ======")
main_content = strip_thought_block(final_system_operations) if final_system_operations else ""
if main_content:
    print(main_content)
else:
    print("(No valid system operations output generated. See above logs.)")




# ---- 6. SEQUENCE DIAGRAM LOOP ----
feedback = ""
approved = False
final_sequence_diagram = None
sequence_diagram_output = None
max_retries = 5  # Maximum retries for invalid outputs per iteration

def strip_thought_block(output: str) -> str:
    """Strip trailing 'Thought:' or similar LLM commentary, returning only the diagram content."""
    if not output:
        return ""
    lower = output.lower()
    idx = lower.find("thought:")
    return output[:idx].strip() if idx != -1 else output.strip()

def is_valid_sequence_diagram(output: str) -> bool:
    """Strictly validate if the output is a sequence diagram (standard UML markup or diagram code), ignoring trailing Thought:."""
    main = strip_thought_block(output)
    if not main or len(main) < 50:
        return False
    diagram_starts = [
        "@startuml",          # PlantUML start
        "```plantuml",        # Markdown PlantUML code block
        "```uml",             # Markdown UML code block
        "```mermaid",         # Mermaid diagram block
        "sequenceDiagram",    # Mermaid sequence diagram
        "participant ",       # PlantUML/Mermaid lifeline
        "+------",            # ASCII-art UML heuristic (box-drawing)
        "|",                  # ASCII-art line
        "->",                 # Typical message arrow in diagrams
        "-->",                # Mermaid/PlantUML arrow
        ": ",                 # Lifeline/message in Mermaid/PlantUML
        "alt ",               # Alt block in PlantUML
        "activate ",          # Activation bars in PlantUML
        "deactivate ",        # Deactivation
    ]
    return any(start in main for start in diagram_starts)

last_attempted_sequence_diagram_output = None  # Store last attempted output
last_nontrivial_sequence_diagram_output = None  # Store best nontrivial output
last_nontrivial_length = 0                      # Track length of best nontrivial output

for iteration in range(max_iterations):
    print(f"\n--- Sequence Diagram Iteration {iteration+1} ---")
    # Validate prerequisite inputs
    if not final_system_operations and not system_operations_output:
        print("Error: No valid system operations available. Skipping to next iteration.")
        feedback = "No valid system operations provided. Ensure system operations are available."
        continue
    if not final_domain_model and not domain_model_output:
        print("Error: No valid domain model available. Skipping to next iteration.")
        feedback = "No valid domain model provided. Ensure domain model is available."
        continue

    sequence_diagram_output = None

    for retry in range(max_retries):
        desc = (
            f"Using the system operations and domain model from previous tasks, create a **UML sequence diagram** for each system operation. "
            "Each diagram must show lifelines for objects (based on domain model classes), messages (method calls), and return messages if appropriate. "
            "Use standard UML sequence diagram notation ONLY.\n"
            "Guidelines:\n"
            "- For each system operation, draw a sequence diagram with:\n"
            "  * The primary actor (stick figure, outside the objects), sending the initial message (found message arrow) to the first system object.\n"
            "  * Lifelines for participating objects shown as rectangles with dashed vertical lines.\n"
            "  * Messages as solid arrows labeled with method names; return messages as dashed arrows labeled with return values if relevant.\n"
            "  * Only objects derived from domain model classes should be shown as lifelines.\n"
            "- Markup—use either graphical UML.\n"
            "Your output must clearly show:\n"
            "  * Stick figure actor (leftmost)\n"
            "  * Object lifelines (rectangles with underlined object names), vertical dashed lines for each lifeline\n"
            "  * Messages (solid arrows labeled with operations)\n"
            "  * Return messages (dashed arrows labeled 'result' or similar, if needed)\n"
        )
        if feedback:
            desc += f"\nReviewer feedback to address: {feedback}\n"
        
        # Summarize inputs to avoid context overflow
        if final_system_operations:
            desc += f"System Operations (summary): {str(final_system_operations)[:500]}...\n"  # Limit to 500 chars
        else:
            desc += f"Latest System Operations (summary): {str(system_operations_output)[:500]}...\n" if system_operations_output else "No system operations available.\n"

        if final_domain_model:
            desc += f"Domain Model (summary): {str(final_domain_model)[:500]}...\n"
        else:
            desc += f"Latest Domain Model (summary): {str(domain_model_output)[:500]}...\n" if domain_model_output else "No domain model available.\n"

        task6 = Task(
            description=desc,
            agent=sequence_diagram_agent,
            expected_output="A standard UML sequence diagram, showing object lifelines, message flows, and collaborations for each system operation. If graphical drawing is not possible, provide a well-labeled ASCII-art UML sequence diagram.",
            context=[task5]
        )
        crew = Crew(
            agents=[sequence_diagram_agent],
            tasks=[task6],
            verbose=True
        )
        
        print(f"Attempt {retry+1}/{max_retries} for Sequence Diagram Generation")
        try:
            result = crew.kickoff()
            sequence_diagram_output = result.tasks_output[0].raw if result.tasks_output else ""
            last_attempted_sequence_diagram_output = sequence_diagram_output  # Always update

            main_content = strip_thought_block(sequence_diagram_output)
            if (
                main_content
                and len(main_content) > last_nontrivial_length
                and is_valid_sequence_diagram(sequence_diagram_output)
            ):
                last_nontrivial_sequence_diagram_output = sequence_diagram_output
                last_nontrivial_length = len(main_content)

            if is_valid_sequence_diagram(sequence_diagram_output):
                print(f"Sequence Diagram Agent Output:\n{sequence_diagram_output}")
                break  # Valid output, proceed to review
            else:
                print(f"Invalid Sequence Diagram Output: {sequence_diagram_output}")
                feedback = (
                    "Invalid or empty sequence diagram. Output must use standard UML notation (graphical), "
                    "with lifelines, message arrows, and return arrows."
                )
                if retry < max_retries - 1:
                    print("Retrying with feedback...")
                else:
                    print("Max retries reached for this iteration.")
        except Exception as e:
            print(f"Error in Sequence Diagram Execution: {str(e)}")
            feedback = (
                f"Execution failed: {str(e)}. Ensure output is a UML sequence diagram (not code)."
            )
            if retry < max_retries - 1:
                print("Retrying...")
                continue
            else:
                print("Max retries reached for this iteration.")
                sequence_diagram_output = ""

    # Do NOT assign to final_sequence_diagram inside the loop; assign at the end.
    if not is_valid_sequence_diagram(sequence_diagram_output):
        print("Error: No valid sequence diagram produced after retries. Continuing to next iteration.")
        feedback = (
            "No valid sequence diagram produced. Ensure output is a standard UML diagram (graphical or ASCII-art) with lifelines, arrows for messages, and labeled interactions."
        )
        continue

    review_desc = (
        f"Review the following sequence diagrams:\n{sequence_diagram_output}\n"
        "Ensure each diagram meets these criteria:\n"
        "- Each system operation is represented by a corresponding sequence diagram with an initial found message from the primary actor (stick figure, leftmost).\n"
        "- Lifelines are objects (rectangles/underlined names) based on domain model classes, each with a vertical dashed line.\n"
        "- Messages are shown as solid arrows labeled with method calls; return messages as dashed arrows, labeled where appropriate.\n"
        "- External actors are not lifelines; actor-initiated operations use found messages.\n"
        "- Diagrams follow standard UML sequence conventions. \n"
        "- Diagrams are complete, clear, and consistent with the system operations and domain model.\n"
        "Return 'APPROVED' if all criteria are met, or 'REJECTED: [specific feedback]' if revisions are needed. "
        "If the output is empty, lacks diagram content, or does not follow UML notation, return 'REJECTED: No valid sequence diagram provided. Output must be a standard UML diagram (graphical or ASCII-art) with lifelines and message flows.'"
    )
    review_task = Task(
        description=review_desc,
        agent=sequence_diagram_reviewer_agent,
        expected_output="Either 'APPROVED' or 'REJECTED: [specific feedback]'",
        context=[task6]
    )
    review_crew = Crew(
        agents=[sequence_diagram_reviewer_agent],
        tasks=[review_task],
        verbose=True
    )
    try:
        review_result = review_crew.kickoff()
        review_output = review_result.tasks_output[0].raw if review_result.tasks_output else ""
        if not review_output:
            print("Error: Sequence Diagram Review produced no output.")
            feedback = "Reviewer failed to produce an output. Ensure the review task is clear and the LLM is functioning."
            continue
        print(f"Sequence Diagram Reviewer Output:\n{review_output}")
    except Exception as e:
        print(f"Error in Sequence Diagram Review: {str(e)}")
        feedback = f"Review failed: {str(e)}. Ensure reviewer produces 'APPROVED' or 'REJECTED: [feedback]'."
        continue

    if "APPROVED" in review_output and is_valid_sequence_diagram(sequence_diagram_output):
        final_sequence_diagram = sequence_diagram_output
        print("✅ Sequence Diagrams Approved!")
        approved = True
        break
    else:
        feedback = review_output.replace("REJECTED:", "").strip() if review_output else "No review output provided."
        print("🔄 Reviewer requested revisions.")

# --- Robust Fallback assignment after all iterations ---
if not final_sequence_diagram or not strip_thought_block(final_sequence_diagram):
    if last_nontrivial_sequence_diagram_output and strip_thought_block(last_nontrivial_sequence_diagram_output):
        final_sequence_diagram = last_nontrivial_sequence_diagram_output
        print("⚠️ Using best nontrivial rejected output as fallback!")
    elif last_attempted_sequence_diagram_output and strip_thought_block(last_attempted_sequence_diagram_output):
        final_sequence_diagram = last_attempted_sequence_diagram_output
        print("⚠️ Using last attempted output as fallback!")
    else:
        final_sequence_diagram = ""
        print("❌ No sequence diagram could be generated.")

print("\n====== FINAL SEQUENCE DIAGRAM OUTPUT ======")
main_content = strip_thought_block(final_sequence_diagram) if final_sequence_diagram else ""
if main_content:
    print(main_content)
else:
    print("(No valid sequence diagram output generated. See above logs.)")





# ---- 7. DESIGN CLASS DIAGRAM LOOP ----
feedback = ""
approved = False
final_design_class_diagram = None
design_class_diagram_output = None
max_retries = 5  # Maximum retries for invalid outputs per iteration

def strip_thought_block(output: str) -> str:
    """Strip trailing 'Thought:' or LLM commentary, returning only the UML diagram."""
    if not output:
        return ""
    lower = output.lower()
    idx = lower.find("thought:")
    return output[:idx].strip() if idx != -1 else output.strip()

def is_valid_design_class_diagram(output: str) -> bool:
    """Strictly validate if the output is a UML design class diagram (standard markup or ASCII-art), ignoring trailing Thought:."""
    main = strip_thought_block(output)
    if not main or len(main) < 50:
        return False
    diagram_starts = [
        "@startuml",           # PlantUML
        "```plantuml",         # Markdown PlantUML code block
        "```uml",              # Markdown UML code block
        "```mermaid",          # Mermaid diagram block
        "classDiagram",        # Mermaid class diagram
        "class ",              # PlantUML/Mermaid class definition
        "+------",             # ASCII-art UML heuristic (box-drawing)
        "|",                   # ASCII-art lines (common in diagrams)
        "--",                  # UML associations (PlantUML/Mermaid/ASCII)
        "<|--",                # Inheritance
        ": ",                  # Attribute/method separator in code diagrams
        "compartment",         # For ASCII-art or textual UML
    ]
    return any(start in main for start in diagram_starts)

last_attempted_design_class_diagram_output = None  # Store last attempted output
last_nontrivial_design_class_diagram_output = None  # Store best available output
last_nontrivial_length = 0                          # Track length of best nontrivial output

for iteration in range(max_iterations):
    print(f"\n--- Design Class Diagram Iteration {iteration+1} ---")
    # Validate prerequisite inputs
    if not final_domain_model and not domain_model_output:
        print("Error: No valid domain model available. Skipping to next iteration.")
        feedback = "No valid domain model provided. Ensure domain model is available."
        continue
    if not final_sequence_diagram and not sequence_diagram_output:
        print("Error: No valid sequence diagrams available. Skipping to next iteration.")
        feedback = "No valid sequence diagrams provided. Ensure sequence diagrams are available."
        continue

    design_class_diagram_output = None

    for retry in range(max_retries):
        desc = (
            f"Using the domain model and sequence diagrams from previous tasks, develop a **UML design class diagram** for the system. "
            "Include classes (rectangles with three compartments: name, attributes, operations), attributes (with data types and visibility), operations (with signatures and visibility), relationships, navigability arrows, and multiplicities, using **standard UML class diagram notation ONLY**.\n"
            "Guidelines:\n"
            "- Base classes and attributes on the domain model, specifying data types (e.g., double, String) and visibility (+ for public, - for private).\n"
            "- Assign operations to classes based on sequence diagram messages (e.g., if :Entity calls performAction() on :Record, include performAction() in Record).\n"
            "- Include relationships with correct navigability arrows and multiplicities, consistent with sequence diagram interactions.\n"
            "- Markup—output must be a graphical UML class diagram.\n"
            "Your diagram must clearly show:\n"
            "  * Each class as a rectangle with three compartments (name, attributes, operations)\n"
            "  * Attributes with [visibility] name: type\n"
            "  * Operations with [visibility] name(parameters): returnType\n"
            "  * Association lines with navigability arrows and labeled multiplicities\n"
        )
        if feedback:
            desc += f"\nReviewer feedback to address: {feedback}\n"
        
        # Summarize inputs
        if final_domain_model:
            desc += f"Domain Model (summary): {str(final_domain_model)[:500]}...\n"
        else:
            desc += f"Latest Domain Model (summary): {str(domain_model_output)[:500]}...\n" if domain_model_output else "No domain model available.\n"
        if final_sequence_diagram:
            desc += f"Sequence Diagrams (summary): {str(final_sequence_diagram)[:500]}...\n"
        else:
            desc += f"Latest Sequence Diagrams (summary): {str(sequence_diagram_output)[:500]}...\n" if sequence_diagram_output else "No sequence diagrams available.\n"

        task7 = Task(
            description=desc,
            agent=design_class_diagram_agent,
            expected_output=(
                "A UML design class diagram in standard UML class diagram notation, showing classes (with three compartments), attributes (with types and visibility), operations (with signatures and visibility), relationships, navigabilities, and multiplicities, consistent with the domain model and sequence diagrams. If graphical drawing is not possible, provide a well-labeled ASCII-art UML class diagram."
            ),
            context=[task4, task6]
        )
        crew = Crew(
            agents=[design_class_diagram_agent],
            tasks=[task7],
            verbose=True
        )
        
        print(f"Attempt {retry+1}/{max_retries} for Design Class Diagram Generation")
        try:
            result = crew.kickoff()
            design_class_diagram_output = result.tasks_output[0].raw if result.tasks_output else ""
            last_attempted_design_class_diagram_output = design_class_diagram_output  # Always update

            main_content = strip_thought_block(design_class_diagram_output)
            if (
                main_content
                and len(main_content) > last_nontrivial_length
                and is_valid_design_class_diagram(design_class_diagram_output)
            ):
                last_nontrivial_design_class_diagram_output = design_class_diagram_output
                last_nontrivial_length = len(main_content)

            if is_valid_design_class_diagram(design_class_diagram_output):
                print(f"Design Class Diagram Agent Output:\n{design_class_diagram_output}")
                break  # Valid output, proceed to review
            else:
                print(f"Invalid Design Class Diagram Output: {design_class_diagram_output}")
                feedback = (
                    "Invalid or empty design class diagram. Output must be in standard UML notation (graphical or ASCII), "
                    "with classes (rectangles with compartments), attributes, operations, and relationships."
                )
                if retry < max_retries - 1:
                    print("Retrying with feedback...")
                else:
                    print("Max retries reached for this iteration.")
        except Exception as e:
            print(f"Error in Design Class Diagram Execution: {str(e)}")
            feedback = (
                f"Execution failed: {str(e)}. Ensure output is a UML class diagram (not code)."
            )
            if retry < max_retries - 1:
                print("Retrying...")
                continue
            else:
                print("Max retries reached for this iteration.")
                design_class_diagram_output = ""
    
    # Do NOT assign to final_design_class_diagram inside the loop; assign at the end.
    if not is_valid_design_class_diagram(design_class_diagram_output):
        print("Error: No valid design class diagram produced after retries. Continuing to next iteration.")
        feedback = (
            "No valid design class diagram produced. Ensure output is a standard UML class diagram (graphical or ASCII-art) "
            "with classes, attributes, operations, relationships, navigability, and multiplicities."
        )
        continue

    review_desc = (
        f"Review the following design class diagram:\n{design_class_diagram_output}\n"
        "Ensure it meets these criteria:\n"
        "- Classes, attributes (with types and visibility), and operations (with signatures and visibility) are consistent with the domain model and sequence diagrams.\n"
        "- Relationships show correct navigability, multiplicity, and use standard UML notation (lines with arrows, multiplicities like '1..*').\n"
        "- Operations are assigned to the correct classes based on sequence diagram message flows.\n"
        "- Visibility indicators (+ for public, - for private) and data types are included for attributes and operations.\n"
        "- Diagram follows encapsulation and cohesion principles.\n"
        "- No missing, ambiguous, or incorrect elements.\n"
        "- UML notation: classes as rectangles with three compartments (name, attributes, operations), attributes as [visibility] name: type, operations as [visibility] name(parameters): returnType, associations with navigability arrows and multiplicities.\n"
        "Return 'APPROVED' if all criteria are met, or 'REJECTED: [specific feedback]' if revisions are needed. "
        "If the output is empty, lacks diagram content, or does not follow UML notation, return 'REJECTED: No valid design class diagram provided. Output must be a UML class diagram (graphical or ASCII-art) with classes, attributes, operations, and relationships.'"
    )
    review_task = Task(
        description=review_desc,
        agent=design_class_diagram_reviewer_agent,
        expected_output="Either 'APPROVED' or 'REJECTED: [specific feedback]'",
        context=[task7]
    )
    review_crew = Crew(
        agents=[design_class_diagram_reviewer_agent],
        tasks=[review_task],
        verbose=True
    )
    try:
        review_result = review_crew.kickoff()
        review_output = review_result.tasks_output[0].raw if review_result.tasks_output else ""
        if not review_output:
            print("Error: Design Class Diagram Review produced no output.")
            feedback = "Reviewer failed to produce an output. Ensure the review task is clear and the LLM is functioning."
            continue
        print(f"Design Class Diagram Reviewer Output:\n{review_output}")
    except Exception as e:
        print(f"Error in Design Class Diagram Review: {str(e)}")
        feedback = f"Review failed: {str(e)}. Ensure reviewer produces 'APPROVED' or 'REJECTED: [feedback]'."
        continue

    if "APPROVED" in review_output and is_valid_design_class_diagram(design_class_diagram_output):
        final_design_class_diagram = design_class_diagram_output
        print("✅ Design Class Diagram Approved!")
        break
    else:
        feedback = review_output.replace("REJECTED:", "").strip() if review_output else "No review output provided."
        print("🔄 Reviewer requested revisions.")

# --- Robust Fallback assignment after all iterations ---
if not final_design_class_diagram or not strip_thought_block(final_design_class_diagram):
    if last_nontrivial_design_class_diagram_output and strip_thought_block(last_nontrivial_design_class_diagram_output):
        final_design_class_diagram = last_nontrivial_design_class_diagram_output
        print("⚠️ Using best nontrivial rejected output as fallback!")
    elif last_attempted_design_class_diagram_output and strip_thought_block(last_attempted_design_class_diagram_output):
        final_design_class_diagram = last_attempted_design_class_diagram_output
        print("⚠️ Using last attempted output as fallback!")
    else:
        final_design_class_diagram = ""
        print("❌ No design class diagram could be generated.")

print("\n====== FINAL DESIGN CLASS DIAGRAM OUTPUT ======")
main_content = strip_thought_block(final_design_class_diagram) if final_design_class_diagram else ""
if main_content:
    print(main_content)
else:
    print("(No valid design class diagram output generated. See above logs.)")





# ---- 8. IMPLEMENTATION LOOP ----
feedback = ""
approved = False
final_implementation = None
implementation_output = None
max_retries = 5  # Maximum retries for invalid outputs per iteration

def strip_thought_block(output: str) -> str:
    """Strip trailing 'Thought:' or LLM commentary, returning only the Java code content."""
    if not output:
        return ""
    lower = output.lower()
    idx = lower.find("thought:")
    return output[:idx].strip() if idx != -1 else output.strip()

def is_valid_implementation(output: str) -> bool:
    """Validate if the output is a valid Java implementation (ignoring trailing Thought:)."""
    main = strip_thought_block(output)
    if not main or len(main) < 50:
        return False
    # Check for Java-like content (e.g., contains class, method signatures, or JUnit annotations)
    return (
        "class " in main or "public " in main or "@Test" in main or "{" in main
    )

last_attempted_implementation_output = None  # Store last attempted output
last_nontrivial_implementation_output = None  # Store best available nontrivial output
last_nontrivial_length = 0  # Track length of best nontrivial output

for iteration in range(max_iterations):
    print(f"\n--- Implementation Iteration {iteration+1} ---")
    # Validate prerequisite inputs
    if not final_design_class_diagram and not design_class_diagram_output:
        print("Error: No valid design class diagram available. Skipping to next iteration.")
        feedback = "No valid design class diagram provided. Ensure design class diagram is available."
        continue
    if not final_sequence_diagram and not sequence_diagram_output:
        print("Error: No valid sequence diagrams available. Skipping to next iteration.")
        feedback = "No valid sequence diagrams provided. Ensure sequence diagrams are available."
        continue

    implementation_output = None

    for retry in range(max_retries):
        desc = (
            f"Using the design class diagram and sequence diagrams from previous tasks, develop a robust Java implementation for the system. "
            "Code must be syntactically correct, with classes structured appropriately (constructors, setters, getters) and methods strictly aligned with design signatures, algorithms, and relationships.\n"
            "Guidelines:\n"
            "- Reflect the class structure, attributes, methods, and relationships (e.g., associations, compositions) from the design class diagram.\n"
            "- Implement behaviors (method logic) as specified in the sequence diagrams, ensuring message flows are accurately coded.\n"
            "- Use proper Java syntax, including visibility (public, private), data types, and method signatures.\n"
            "- Follow Java coding conventions (e.g., camelCase for methods, PascalCase for classes).\n"
            "- Example implementation:\n"
            "  ```java\n"
            "  public class Entity {\n"
            "      private double value;\n"
            "      private String owner;\n"
            "      private List<Record> records;\n"
            "      public Entity(String owner, double value) {\n"
            "          this.owner = owner;\n"
            "          this.value = value;\n"
            "          this.records = new ArrayList<>();\n"
            "      }\n"
            "      public boolean performAction(double amount) {\n"
            "          if (amount <= value) {\n"
            "              value -= amount;\n"
            "              records.add(new Record(amount));\n"
            "              return true;\n"
            "          }\n"
            "          return false;\n"
            "      }\n"
            "  }\n"
            "  public class Record {\n"
            "      private double amount;\n"
            "      private String timestamp;\n"
            "      public Record(double amount) {\n"
            "          this.amount = amount;\n"
            "          this.timestamp = new Date().toString();\n"
            "      }\n"
            "  }\n"
            "  ```\n"
            "Ensure the code is syntactically correct, follows Java conventions, and aligns with the provided diagrams.\n"
        )
        if feedback:
            desc += f"\nReviewer feedback to address: {feedback}\n"

        # Summarize inputs to avoid context overflow
        if final_design_class_diagram:
            desc += f"Design Class Diagram (summary): {str(final_design_class_diagram)[:500]}...\n"
        else:
            desc += f"Latest Design Class Diagram (summary): {str(design_class_diagram_output)[:500]}...\n" if design_class_diagram_output else "No design class diagram available.\n"
        
        if final_sequence_diagram:
            desc += f"Sequence Diagrams (summary): {str(final_sequence_diagram)[:500]}...\n"
        else:
            desc += f"Latest Sequence Diagrams (summary): {str(sequence_diagram_output)[:500]}...\n" if sequence_diagram_output else "No sequence diagrams available.\n"

        task8 = Task(
            description=desc,
            agent=implementation_agent,
            expected_output="A syntactically correct Java implementation with classes, attributes, methods, and relationships aligned with the design class and sequence diagrams, including optional JUnit 5 tests.",
            context=[task7]
        )
        crew = Crew(
            agents=[implementation_agent],
            tasks=[task8],
            verbose=True
        )
        
        print(f"Attempt {retry+1}/{max_retries} for Implementation Generation")
        try:
            result = crew.kickoff()
            implementation_output = result.tasks_output[0].raw if result.tasks_output else ""
            last_attempted_implementation_output = implementation_output  # Always update with last

            main_content = strip_thought_block(implementation_output)
            if (
                main_content
                and len(main_content) > last_nontrivial_length
                and is_valid_implementation(implementation_output)
            ):
                last_nontrivial_implementation_output = implementation_output
                last_nontrivial_length = len(main_content)

            if is_valid_implementation(implementation_output):
                print(f"Implementation Agent Output:\n{implementation_output}")
                break  # Valid output, proceed to review
            else:
                print(f"Invalid Implementation Output: {implementation_output}")
                feedback = "Invalid or empty Java implementation. Ensure output is syntactically correct Java code with classes, methods, and relationships as shown in the example."
                if retry < max_retries - 1:
                    print("Retrying with feedback...")
                else:
                    print("Max retries reached for this iteration.")
        except Exception as e:
            print(f"Error in Implementation Execution: {str(e)}")
            feedback = f"Execution failed: {str(e)}. Ensure output is syntactically correct Java code."
            if retry < max_retries - 1:
                print("Retrying...")
                continue
            else:
                print("Max retries reached for this iteration.")
                implementation_output = ""
    
    # Do NOT assign to final_implementation inside the loop; assign at the end.
    if not is_valid_implementation(implementation_output):
        print("Error: No valid Java implementation produced after retries. Continuing to next iteration.")
        feedback = "No valid Java implementation produced. Ensure output is syntactically correct Java code with classes, methods, and relationships."
        continue

    review_desc = (
        f"Review the following Java implementation:\n{implementation_output}\n"
        "Ensure it meets these criteria:\n"
        "- Code structure (classes, attributes, methods, relationships) precisely matches the design class and sequence diagrams.\n"
        "- Method signatures, parameters, visibility, and data types reflect the design class diagram.\n"
        "- Object interactions and algorithms align with the sequence diagrams.\n"
        "- Code is syntactically correct, free of logical errors, and follows Java coding conventions.\n"
        "- Constructors, getters, setters, and encapsulation are properly implemented.\n"
        "- Class relationships (e.g., composition, inheritance, association) are correctly implemented.\n"
        "- Optional JUnit 5 tests use proper annotations (@Test, @BeforeEach, @AfterEach) and test key functionality.\n"
        "Return 'APPROVED' if all criteria are met, or 'REJECTED: [specific feedback]' if revisions are needed. "
        "If the output is empty, lacks Java code (e.g., contains only thoughts like 'Thought:'), or is syntactically incorrect, return 'REJECTED: No valid Java implementation provided. Output must be syntactically correct Java code with classes, methods, and relationships.'"
    )
    review_task = Task(
        description=review_desc,
        agent=implementation_reviewer_agent,
        expected_output="Either 'APPROVED' or 'REJECTED: [specific feedback]'",
        context=[task8]
    )
    review_crew = Crew(
        agents=[implementation_reviewer_agent],
        tasks=[review_task],
        verbose=True
    )
    try:
        review_result = review_crew.kickoff()
        review_output = review_result.tasks_output[0].raw if review_result.tasks_output else ""
        if not review_output:
            print("Error: Implementation Review produced no output.")
            feedback = "Reviewer failed to produce an output. Ensure the review task is clear and the LLM is functioning."
            continue
        print(f"Implementation Reviewer Output:\n{review_output}")
    except Exception as e:
        print(f"Error in Implementation Review: {str(e)}")
        feedback = f"Review failed: {str(e)}. Ensure reviewer produces 'APPROVED' or 'REJECTED: [feedback]'."
        continue

    if "APPROVED" in review_output and is_valid_implementation(implementation_output):
        final_implementation = implementation_output
        print("✅ Implementation Approved!")
        break
    else:
        feedback = review_output.replace("REJECTED:", "").strip() if review_output else "No review output provided."
        print("🔄 Reviewer requested revisions.")

# --- Robust Fallback assignment after all iterations ---
if not final_implementation or not strip_thought_block(final_implementation):
    if last_nontrivial_implementation_output and strip_thought_block(last_nontrivial_implementation_output):
        final_implementation = last_nontrivial_implementation_output
        print("⚠️ Using best nontrivial rejected output as fallback!")
    elif last_attempted_implementation_output and strip_thought_block(last_attempted_implementation_output):
        final_implementation = last_attempted_implementation_output
        print("⚠️ Using last attempted output as fallback!")
    else:
        final_implementation = ""
        print("❌ No implementation output could be generated.")

print("\n====== FINAL IMPLEMENTATION OUTPUT ======")
main_content = strip_thought_block(final_implementation) if final_implementation else ""
if main_content:
    print(main_content)
else:
    print("(No valid implementation output generated. See above logs.)")





# ---- 9. TESTING LOOP ----
feedback = ""
approved = False
final_testing = None
testing_output = None
max_retries = 5  # Maximum retries for invalid outputs per iteration

def strip_thought_block(output: str) -> str:
    """Strip trailing 'Thought:' or LLM commentary, returning only the JUnit code content."""
    if not output:
        return ""
    lower = output.lower()
    idx = lower.find("thought:")
    return output[:idx].strip() if idx != -1 else output.strip()

def is_valid_test_suite(output: str) -> bool:
    """Validate if the output is a valid JUnit 5 test suite, ignoring trailing Thought:."""
    main = strip_thought_block(output)
    if not main or len(main) < 50:
        return False
    # Check for JUnit 5 test content (class, @Test, assert, etc)
    return (
        "@Test" in main or "assert" in main or "class " in main or "@BeforeEach" in main
    )

last_attempted_testing_output = None  # Store last attempted output
last_nontrivial_testing_output = None  # Store best available nontrivial output
last_nontrivial_length = 0  # Track length of best nontrivial output

for iteration in range(max_iterations):
    print(f"\n--- Testing Iteration {iteration+1} ---")
    # Validate prerequisite inputs
    if not final_implementation and not implementation_output:
        print("Error: No valid implementation available. Skipping to next iteration.")
        feedback = "No valid Java implementation provided. Ensure implementation is available."
        continue

    testing_output = None

    for retry in range(max_retries):
        desc = (
            f"Based on the Java implementation from the previous task, develop a comprehensive JUnit 5 test suite for the system. "
            "Include unit tests for individual methods, integration tests for class interactions, and system tests for complete use case scenarios. "
            "Use @Test, @BeforeEach, and @AfterEach annotations where appropriate, with clear assertions and setup/teardown procedures.\n"
            "Guidelines:\n"
            "- Unit tests must cover all public methods in all classes.\n"
            "- Integration tests must validate key interactions from sequence diagrams.\n"
            "- System tests must cover complete scenarios from use case specifications and requirements.\n"
            "- Use JUnit 5 assertions (e.g., assertEquals, assertTrue) and follow Java test conventions.\n"
            "- Example test suite:\n"
            "  ```java\n"
            "  import org.junit.jupiter.api.BeforeEach;\n"
            "  import org.junit.jupiter.api.Test;\n"
            "  import static org.junit.jupiter.api.Assertions.*;\n"
            "  public class EntityTest {\n"
            "      private Entity entity;\n"
            "      @BeforeEach\n"
            "      void setUp() {\n"
            "          entity = new Entity(\"User\", 100.0);\n"
            "      }\n"
            "      @Test\n"
            "      void testPerformAction() {\n"
            "          boolean result = entity.performAction(50.0);\n"
            "          assertTrue(result);\n"
            "          assertEquals(50.0, entity.getValue(), 0.01);\n"
            "      }\n"
            "      @Test\n"
            "      void testPerformActionInvalidInput() {\n"
            "          boolean result = entity.performAction(150.0);\n"
            "          assertFalse(result);\n"
            "          assertEquals(100.0, entity.getValue(), 0.01);\n"
            "      }\n"
            "  }\n"
            "  ```\n"
            "Ensure the test suite is syntactically correct, covers all test levels, and includes clear assertions.\n"
        )
        if feedback:
            desc += f"\nReviewer feedback to address: {feedback}\n"

        # Summarize inputs to avoid context overflow
        if final_implementation:
            desc += f"Implementation (summary): {str(final_implementation)[:500]}...\n"
        else:
            desc += f"Latest Implementation (summary): {str(implementation_output)[:500]}...\n" if implementation_output else "No implementation available.\n"

        task9 = Task(
            description=desc,
            agent=testing_agent,
            expected_output="A comprehensive JUnit 5 test suite with unit, integration, and system tests, including clear assertions, proper setup/teardown routines, and alignment with the Java implementation.",
            context=[task8]
        )
        crew = Crew(
            agents=[testing_agent],
            tasks=[task9],
            verbose=True
        )
        
        print(f"Attempt {retry+1}/{max_retries} for Testing Generation")
        try:
            result = crew.kickoff()
            testing_output = result.tasks_output[0].raw if result.tasks_output else ""
            last_attempted_testing_output = testing_output  # Always update with last

            main_content = strip_thought_block(testing_output)
            if (
                main_content
                and len(main_content) > last_nontrivial_length
                and is_valid_test_suite(testing_output)
            ):
                last_nontrivial_testing_output = testing_output
                last_nontrivial_length = len(main_content)

            if is_valid_test_suite(testing_output):
                print(f"Testing Agent Output:\n{testing_output}")
                break  # Valid output, proceed to review
            else:
                print(f"Invalid Testing Output: {testing_output}")
                feedback = "Invalid or empty test suite. Ensure output is a syntactically correct JUnit 5 test suite with unit, integration, and system tests as shown in the example."
                if retry < max_retries - 1:
                    print("Retrying with feedback...")
                else:
                    print("Max retries reached for this iteration.")
        except Exception as e:
            print(f"Error in Testing Execution: {str(e)}")
            feedback = f"Execution failed: {str(e)}. Ensure output is a syntactically correct JUnit 5 test suite."
            if retry < max_retries - 1:
                print("Retrying...")
                continue
            else:
                print("Max retries reached for this iteration.")
                testing_output = ""
    
    # Do NOT assign to final_testing inside the loop; assign at the end.
    if not is_valid_test_suite(testing_output):
        print("Error: No valid test suite produced after retries. Continuing to next iteration.")
        feedback = "No valid JUnit 5 test suite produced. Ensure output is syntactically correct with unit, integration, and system tests."
        continue

    review_desc = (
        f"Review the following JUnit 5 test suite:\n{testing_output}\n"
        "Ensure it meets these criteria:\n"
        "- Unit tests cover all public methods in all classes from the implementation.\n"
        "- Integration tests validate key class and method interactions as depicted in sequence diagrams.\n"
        "- System tests exercise complete use case scenarios and requirements.\n"
        "- Assertions are clear, logically structured, and validate expected behavior.\n"
        "- Tests include proper setup (@BeforeEach) and teardown (@AfterEach) routines where needed.\n"
        "- Test cases are readable, maintainable, and follow JUnit 5 conventions (e.g., @Test, assertEquals).\n"
        "- The suite produces clear pass/fail results and supports diagnosis of failures.\n"
        "Return 'APPROVED' if all criteria are met, or 'REJECTED: [specific feedback]' if revisions are needed. "
        "If the output is empty, lacks JUnit 5 test code (e.g., contains only thoughts like 'Thought:'), or is syntactically incorrect, return 'REJECTED: No valid JUnit 5 test suite provided. Output must be syntactically correct with unit, integration, and system tests.'"
    )
    review_task = Task(
        description=review_desc,
        agent=testing_reviewer_agent,
        expected_output="Either 'APPROVED' or 'REJECTED: [specific feedback]'",
        context=[task9]
    )
    review_crew = Crew(
        agents=[testing_reviewer_agent],
        tasks=[review_task],
        verbose=True
    )
    try:
        review_result = review_crew.kickoff()
        review_output = review_result.tasks_output[0].raw if review_result.tasks_output else ""
        if not review_output:
            print("Error: Testing Review produced no output.")
            feedback = "Reviewer failed to produce an output. Ensure the review task is clear and the LLM is functioning."
            continue
        print(f"Testing Reviewer Output:\n{review_output}")
    except Exception as e:
        print(f"Error in Testing Review: {str(e)}")
        feedback = f"Review failed: {str(e)}. Ensure reviewer produces 'APPROVED' or 'REJECTED: [feedback]'."
        continue

    if "APPROVED" in review_output and is_valid_test_suite(testing_output):
        final_testing = testing_output
        print("✅ Testing Approved!")
        break
    else:
        feedback = review_output.replace("REJECTED:", "").strip() if review_output else "No review output provided."
        print("🔄 Reviewer requested revisions.")

# --- Robust Fallback assignment after all iterations ---
if not final_testing or not strip_thought_block(final_testing):
    if last_nontrivial_testing_output and strip_thought_block(last_nontrivial_testing_output):
        final_testing = last_nontrivial_testing_output
        print("⚠️ Using best nontrivial rejected output as fallback!")
    elif last_attempted_testing_output and strip_thought_block(last_attempted_testing_output):
        final_testing = last_attempted_testing_output
        print("⚠️ Using last attempted output as fallback!")
    else:
        final_testing = ""
        print("❌ No testing output could be generated.")

print("\n====== FINAL TESTING OUTPUT ======")
main_content = strip_thought_block(final_testing) if final_testing else ""
if main_content:
    print(main_content)
else:
    print("(No valid testing output generated. See above logs.)")





# Final Crew Execution
crew = Crew(
    agents=[
        requirements_identifier_agent,
        use_case_modeler_agent,
        use_case_specification_agent,
        domain_modeling_agent,
        system_operations_agent,
        sequence_diagram_agent,
        design_class_diagram_agent,
        implementation_agent,
        testing_agent
    ],
    tasks=[
        task1, task2, task3, task4, task5, task6, task7, task8, task9
    ],
    process="sequential",
    full_output=True,
    verbose=True
)

# Run Crew
try:
    result = crew.kickoff()
    for i, task in enumerate(crew.tasks):
        print(f"Task {i+1}: {task.description}")
        print(f"Raw Output: {task.output.raw}")
except Exception as e:
    print(f"Error in Final Crew Execution: {str(e)}")


--- Requirements Identification Iteration 1 ---
Attempt 1/5 for Requirements Identification


╭──────────────────────────────────────────── Crew Execution Started ─────────────────────────────────────────────╮
│                                                                                                                 │
│  Crew Execution Started                                                                                         │
│  Name: crew                                                                                                     │
│  ID: ff0a7cd2-603e-452b-b7ff-0f8679a03bba                                                                       │
│  Tool Args:                                                                                                     │
│                                                                                                                 │
│                                                                                                                 │
╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╯

╭─────────────────────────────────────────────── 🤖 Agent Started ────────────────────────────────────────────────╮
│                                                                                                                 │
│  Agent: Requirements Identification Expert                                                                      │
│                                                                                                                 │
│  Task: ### System Description                                                                                   │
│  A food order and delivery system should offer a convenient and efficient way for users to explore, order, and  │
│  receive meals from a wide range of local and international cuisines. It should provide an accessible and       │
│  easy-to-navigate interface, available on both web and mobile platforms, where users can browse menus, read     │
│  reviews, and customize orders to their preferences. The system should feature real-time order tracking,        │
│  estimated delivery times, and notifications to keep users updated from the moment an order is placed until it  │
│  is delivered. Integration with various payment gateways should ensure secure and flexible payment options.     │
│  Additionally, the system should support promotional features, loyalty programs, and personalized               │
│  recommendations based on user preferences and order history, enhancing the overall user experience and         │
│  encouraging repeat business.                                                                                   │
│                                                                                                                 │
│  ### Task                                                                                                       │
│  Identify and categorize functional and non-functional requirements for the above system. Produce a structured  │
│  text list with uniquely identified requirements, categorized as Functional Requirements (FR) and               │
│  Non-Functional Requirements (NFR). Each requirement must have a unique ID (e.g., FR1, NFR1) and a clear        │
│  description.                                                                                                   │
│                                                                                                                 │
│  Guidelines:                                                                                                    │
│  - Functional requirements describe specific system actions (e.g., 'User can perform an action').               │
│  - Non-functional requirements describe system qualities or constraints (e.g., 'System must ensure secure       │
│  operations').                                                                                                  │
│  - Use a clear, organized format, e.g.:                                                                         │
│    Functional Requirements:                                                                                     │
│      FR1: User can perform an action with specified parameters.                                                 │
│      FR2: User can view activity history.                                                                       │
│    Non-Functional Requirements:                                                                                 │
│      NFR1: System must ensure secure operations.                                                                │
│      NFR2: System response time must be under 2 seconds.                                                        │
│  If no system description is provided, generate a sample requirements list for a generic system.                │
│  Ensure all requirements are clear, traceable to the system description, and categorized appropriately.         │
│                                                        

╭───────────────────────────────────────────── ✅ Agent Final Answer ─────────────────────────────────────────────╮
│                                                                                                                 │
│  Agent: Requirements Identification Expert                                                                      │
│                                                                                                                 │
│  Final Answer:                                                                                                  │
│  Thought: I now can give a great answer                                                                         │
│                                                                                                                 │
╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╯

╭──────────────────────────────────────────────── Task Completion ────────────────────────────────────────────────╮
│                                                                                                                 │
│  Task Completed                                                                                                 │
│  Name: 9f74a375-46e6-4302-a2b7-0eb3fc3b5bf4                                                                     │
│  Agent: Requirements Identification Expert                                                                      │
│  Tool Args:                                                                                                     │
│                                                                                                                 │
│                                                                                                                 │
╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╯

...

╭─────────────────────────────────────────────── 🤖 Agent Started ────────────────────────────────────────────────╮
│                                                                                                                 │
│  Agent: Testing Expert                                                                                          │
│                                                                                                                 │
│  Task: Based on the Java implementation from the previous task, develop a comprehensive JUnit 5 test suite for  │
│  the system. Include unit tests for individual methods, integration tests for class interactions, and system    │
│  tests for complete use case scenarios. Use @Test, @BeforeEach, and @AfterEach annotations where appropriate,   │
│  with clear assertions and setup/teardown procedures.                                                           │
│  Guidelines:                                                                                                    │
│  - Unit tests must cover all public methods in all classes.                                                     │
│  - Integration tests must validate key interactions from sequence diagrams.                                     │
│  - System tests must cover complete scenarios from use case specifications and requirements.                    │
│  - Use JUnit 5 assertions (e.g., assertEquals, assertTrue) and follow Java test conventions.                    │
│  - Example test suite:                                                                                          │
│    ```java                                                                                                      │
│    import org.junit.jupiter.api.BeforeEach;                                                                     │
│    import org.junit.jupiter.api.Test;                                                                           │
│    import static org.junit.jupiter.api.Assertions.*;                                                            │
│    public class EntityTest {                                                                                    │
│        private Entity entity;                                                                                   │
│        @BeforeEach                                                                                              │
│        void setUp() {                                                                                           │
│            entity = new Entity("User", 100.0);                                                                  │
│        }                                                                                                        │
│        @Test                                                                                                    │
│        void testPerformAction() {                                                                               │
│            boolean result = entity.performAction(50.0);                                                         │
│            assertTrue(result);                                                                                  │
│            assertEquals(50.0, entity.getValue(), 0.01);                                                         │
│        }                                                                                                        │
│        @Test                                                                                                    │
│        void testPerformActionInvalidInput() {                                                                   │
│            boolean result = entity.performAction(150.0);                                                        │
│            assertFalse(result);                                                                                 │
│            assertEquals(100.0, entity.getValue(), 0.01)

╭───────────────────────────────────────────── ✅ Agent Final Answer ─────────────────────────────────────────────╮
│                                                                                                                 │
│  Agent: Testing Expert                                                                                          │
│                                                                                                                 │
│  Final Answer:                                                                                                  │
│  ```java                                                                                                        │
│  import org.junit.jupiter.api.BeforeEach;                                                                       │
│  import org.junit.jupiter.api.Test;                                                                             │
│  import static org.junit.jupiter.api.Assertions.*;                                                              │
│  import java.util.Set;                                                                                          │
│                                                                                                                 │
│  public class UserTest {                                                                                        │
│                                                                                                                 │
│      private User user;                                                                                         │
│      @BeforeEach                                                                                                │
│      void setUp() {                                                                                             │
│          user = new User("John Doe", "johndoe@example.com", "password123");                                     │
│      }                                                                                                          │
│                                                                                                                 │
│      // Unit tests for individual methods                                                                       │
│                                                                                                                 │
│      @Test                                                                                                      │
│      void testGetName() {                                                                                       │
│          assertEquals("John Doe", user.getName());                                                              │
│      }                                                                                                          │
│                                                                                                                 │
│      @Test                                                                                                      │
│      void testGetEmail() {                                                                                      │
│          assertEquals("johndoe@example.com", user.getEmail());                                                  │
│      }                                                                                                          │
│                                                                                                                 │
│      @Test                                                                                                      │
│      void testGetPassword() {                                                                                   │
│          assertNotNull(user.getPassword());                                                                     │
│      }                                                 

╭──────────────────────────────────────────────── Task Completion ────────────────────────────────────────────────╮
│                                                                                                                 │
│  Task Completed                                                                                                 │
│  Name: 431c4f9f-278e-428e-9933-ea1e7bfee32e                                                                     │
│  Agent: Testing Expert                                                                                          │
│  Tool Args:                                                                                                     │
│                                                                                                                 │
│                                                                                                                 │
╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────────╯

╭──────────────────────────────────────────────── Crew Completion ────────────────────────────────────────────────╮
│                                                                                                                 │
│  Crew Execution Completed                                                                                       │
│  Name: crew                                                                                                     │
│  ID: d4065c28-b3fb-4e0e-9db6-4dceeca454b3                                                                       │
│  Tool Args:                                                                                                     │
│  Final Output: ```java                                                                                          │
│  import org.junit.jupiter.api.BeforeEach;                                                                       │
│  import org.junit.jupiter.api.Test;                                                                             │
│  import static org.junit.jupiter.api.Assertions.*;                                                              │
│  import java.util.Set;                                                                                          │
│                                                                                                                 │
│  public class UserTest {                                                                                        │
│                                                                                                                 │
│      private User user;                                                                                         │
│      @BeforeEach                                                                                                │
│      void setUp() {                                                                                             │
│          user = new User("John Doe", "johndoe@example.com", "password123");                                     │
│      }                                                                                                          │
│                                                                                                                 │
│      // Unit tests for individual methods                                                                       │
│                                                                                                                 │
│      @Test                                                                                                      │
│      void testGetName() {                                                                                       │
│          assertEquals("John Doe", user.getName());                                                              │
│      }                                                                                                          │
│                                                                                                                 │
│      @Test                                                                                                      │
│      void testGetEmail() {                                                                                      │
│          assertEquals("johndoe@example.com", user.getEmail());                                                  │
│      }                                                                                                          │
│                                                                                                                 │
│      @Test                                                                                                      │
│      void testGetPassword() {                                                                                   │
│          assertNotNull(user.getPassword());           

Task 1: ### System Description
A food order and delivery system should offer a convenient and efficient way for users to explore, order, and receive meals from a wide range of local and international cuisines. It should provide an accessible and easy-to-navigate interface, available on both web and mobile platforms, where users can browse menus, read reviews, and customize orders to their preferences. The system should feature real-time order tracking, estimated delivery times, and notifications to keep users updated from the moment an order is placed until it is delivered. Integration with various payment gateways should ensure secure and flexible payment options. Additionally, the system should support promotional features, loyalty programs, and personalized recommendations based on user preferences and order history, enhancing the overall user experience and encouraging repeat business.

### Task
Identify and categorize functional and non-functional requirements for the above system